In [220]:
# Scrape, clean, and upload data to database solution   

import pandas as pd
import numpy as np
import requests
import sys
import os
import json
from concurrent.futures import ProcessPoolExecutor


#read data to see what the fuck it looks like
with open('/Users/collinkennedy/Dropbox/R_dropbox/Zelus_Analytics/odis_json/64827.json', 'r') as file:
    json_data = json.load(file)


folder_path = "/Users/collinkennedy/Dropbox/R_dropbox/Zelus_Analytics/test_json"
# def process_json_file(file_path):
#     with open(file_path, 'r') as file:
#         json_data = json.load(file)
#         # Perform data preprocessing on the json_data
#         # Return the preprocessed data
#         return (json_data)
#
file_paths = [os.path.join(folder_path, filename) for filename in os.listdir(folder_path) if filename.endswith('.json')]




In [221]:
file_paths

['/Users/collinkennedy/Dropbox/R_dropbox/Zelus_Analytics/test_json/64817.json',
 '/Users/collinkennedy/Dropbox/R_dropbox/Zelus_Analytics/test_json/64816.json',
 '/Users/collinkennedy/Dropbox/R_dropbox/Zelus_Analytics/test_json/64820.json',
 '/Users/collinkennedy/Dropbox/R_dropbox/Zelus_Analytics/test_json/64819.json',
 '/Users/collinkennedy/Dropbox/R_dropbox/Zelus_Analytics/test_json/64815.json',
 '/Users/collinkennedy/Dropbox/R_dropbox/Zelus_Analytics/test_json/64814.json']

In [206]:
json_data

{'meta': {'data_version': '1.1.0', 'created': '2023-01-13', 'revision': 1},
 'info': {'balls_per_over': 6,
  'city': 'Bridgetown',
  'dates': ['2003-06-07'],
  'event': {'name': 'Sri Lanka tour of West Indies', 'match_number': 1},
  'gender': 'male',
  'match_type': 'ODI',
  'match_type_number': 2022,
  'officials': {'match_referees': ['Wasim Raja'],
   'tv_umpires': ['EA Nicholls'],
   'umpires': ['BF Bowden', 'BR Doctrove']},
  'outcome': {'winner': 'Sri Lanka', 'by': {'runs': 55}},
  'overs': 50,
  'player_of_match': ['M Muralitharan'],
  'players': {'Sri Lanka': ['ST Jayasuriya',
    'RS Kaluwitharana',
    'MS Atapattu',
    'KC Sangakkara',
    'DPMD Jayawardene',
    'TM Dilshan',
    'HDPK Dharmasena',
    'WPUJC Vaas',
    'M Muralitharan',
    'RAP Nissanka',
    'D Gamage'],
   'West Indies': ['CH Gayle',
    'WW Hinds',
    'RL Powell',
    'RR Sarwan',
    'BC Lara',
    'MN Samuels',
    'RD Jacobs',
    'DE Bernard',
    'VC Drakes',
    'M Dillon',
    'CD Collymore']},

In [4]:
json_data['info']['teams']

['New Zealand', 'India']

In [62]:
json_data['info']

{'balls_per_over': 6,
 'city': 'Dunedin',
 'dates': ['2012-02-03'],
 'event': {'match_number': 1, 'name': 'Zimbabwe in New Zealand ODI Series'},
 'gender': 'male',
 'match_type': 'ODI',
 'match_type_number': 3230,
 'officials': {'match_referees': ['DC Boon'],
  'reserve_umpires': ['GAV Baxter'],
  'tv_umpires': ['RJ Tucker'],
  'umpires': ['Enamul Haque', 'CB Gaffaney']},
 'outcome': {'by': {'runs': 90}, 'winner': 'New Zealand'},
 'overs': 50,
 'player_of_match': ['MJ Guptill'],
 'players': {'New Zealand': ['RJ Nicol',
   'MJ Guptill',
   'BB McCullum',
   'KS Williamson',
   'TWM Latham',
   'DG Brownlie',
   'NL McCullum',
   'AM Ellis',
   'DAJ Bracewell',
   'KD Mills',
   'TG Southee'],
  'Zimbabwe': ['H Masakadza',
   'S Matsikenyeri',
   'RW Chakabva',
   'BRM Taylor',
   'T Taibu',
   'MN Waller',
   'E Chigumbura',
   'KO Meth',
   'SW Masakadza',
   'RW Price',
   'KM Jarvis']},
 'registry': {'people': {'AM Ellis': 'f987245c',
   'BB McCullum': 'b8a55852',
   'BRM Taylor': '5

Player Data

Matches Data test:


Players Table and Teams table first

In [19]:


#this function is used to produce a player_df and team_df

#both of those dataframes are then written to the players and teams table in the cricket_db, respectively
def parse_team_player_info(json_data: dict):
    """
    takes json data as

    Parameters:
    --------------
    - json_data (dict) : json object as a dictionary


    Returns:
    -------------
    - player_df (pandas DataFrame): 
    
    
    """
    player_columns = [
        "team",
        "player_name",
        "registryID"
    ]

    temp_people = json_data['info']['registry']['people']
    temp_teams = json_data['info']['teams']
    
    player_df = pd.DataFrame(columns = player_columns)
    for team in temp_teams:
        #for each team, get the players on that team, for each player, get their registry id as well

        for player in json_data['info']['players'][team]: 

            registryId = temp_people[player]

            # print("team: {}, player: {}, registryId: {} ".format(team,player, registryId))
            
            temp_df = pd.DataFrame({"team": [team], "player_name": [player], "registryID": [registryId]})

            player_df = pd.concat([player_df,temp_df], axis = 0)
        
    team_df = player_df[['team']].drop_duplicates() #drop duplicates
    player_df = player_df[['player_name','registryID']]
    return team_df, player_df

In [ ]:
team_df,player_df = parse_team_player_info(json_data = json_data)

In [210]:
import mysql.connector
import sqlalchemy

#connect to MySQL database cricket_db
cnx = mysql.connector.connect(user='webmaster', password='Zelus2cool123',
                              database='cricket_db')



In [215]:
def write_players_to_cricket_db(player_df: pd.DataFrame):
    """Writes player data to players table in cricket_db"""
    table_name = 'players'
    columns = ', '.join(player_df.columns)
    sql = f"INSERT INTO {table_name} ({columns}) VALUES ({', '.join(['%s'] * len(player_df.columns))})"

    # Execute the INSERT statement for each row
    cursor = cnx.cursor()
    for row in player_df.itertuples(index=False):
        try:
            cursor.execute(sql, row)
            cnx.commit()
            print(f"1 row inserted successfully into {table_name} table!")
        except mysql.connector.IntegrityError:
            print("Duplicate! Skipping...")

    cursor.close()


In [212]:
def write_teams_to_cricket_db(team_df: pd.DataFrame):
    """Write unique teams to teams table in cricket_db"""
    table_name = 'teams'
    columns = ', '.join(team_df.columns)
    sql = f"INSERT INTO {table_name} ({columns}) VALUES ({', '.join(['%s'] * len(team_df.columns))})"

    # Execute the INSERT statement for each row
    cursor = cnx.cursor()
    for row in team_df.itertuples(index=False):
        try:
            cursor.execute(sql, row)
            cnx.commit()
            print(f"1 row inserted successfully into {table_name} table!")
        except mysql.connector.IntegrityError:
            print("Duplicate! Skipping...")

    cursor.close()

In [213]:
test_df = pd.DataFrame({"team": ['New Zealand', 'Britian']})

In [208]:
test_df

team
0  New Zealand
1      Britian

In [214]:
write_teams_to_cricket_db(team_df=test_df)

Duplicate! Skipping...
1 row inserted successfully into teams table!


Now lets get the basic match information

In [328]:
def parse_match_info(json_data: dict):

    """ parse that match info from the json and return a named dataframe """

    #balls per over
    balls_per_over = json_data['info']['balls_per_over']

    #city
    try:
        city = json_data['info']['city']
    except KeyError:
        city = "no city field"

    #date start
    date_start = json_data['info']['dates'][0]

    #date end
    date_end = json_data['info']['dates'][-1] #latest date

    #match name
    try:
        match_name = json_data['info']['event']['name']
    except:
        match_name = None

    #match number
    try:
        match_number = json_data['info']['event']['match_number']
    except KeyError:
        match_number = None

    #gender
    gender = json_data['info']['gender']

    #match type
    match_type = json_data['info']['match_type']

    #match_type_number
    match_type_number = json_data['info']['match_type_number']

    #offical_data
    official_data = json_data['info']['officials'] #just store as json for now

    #winner
    try:
        winner = json_data['info']['outcome']['winner']
    except:
        winner = json_data['info']['outcome']['result'] #this will happen in the case of a tie, for example


    #decision_by
    try:
        decision_by = list(json_data['info']['outcome']['by'].keys())[0]
    except:
        decision_by = json_data['info']['outcome']['result']

    #overs
    overs = json_data['info']['overs']

    #player_of_match
    try:
        player_of_match = json_data['info']['player_of_match'][0]
    except KeyError:
        player_of_match = "no PoM field"

    #team1
    team1 = list(json_data['info']['players'].keys())[0]

    print("team1", team1)

    #team1_players
    team1_players = json_data['info']['players'][team1]

    #team2
    team2 = list(json_data['info']['players'].keys())[1]
    print("team2: ", team2)


    #team2_players
    team2_players = json_data['info']['players'][team2]

    #season
    season = json_data['info']['season']

    #team_type
    team_type = json_data['info']['team_type']

    #toss_decision
    toss_decision = json_data['info']['toss']['decision']

    #toss_winner
    toss_winner = json_data['info']['toss']['winner']

    #venue
    venue = json_data['info']['venue']

    

    #get the team1 and team2 id— team data is always written first so this should always exist before writing the match info data
    cursor = cnx.cursor()
    cursor.execute("SELECT team_id FROM cricket_db.teams WHERE team = '{}'".format(team1))
    result = cursor.fetchall()  # Fetch any remaining results
    cursor.close()
    print(result)
    team1_id = result[0][0]

    cursor = cnx.cursor()
    cursor.execute("SELECT team_id FROM cricket_db.teams WHERE team = '{}'".format(team2))
    result = cursor.fetchall()  # Fetch any remaining results
    cursor.close()
    team2_id = result[0][0]


    # match_info_df = pd.DataFrame(columns = match_info_columns)

    match_info_df = pd.DataFrame({
        "balls_per_over": [balls_per_over],
        "city": [city],
        "date_start": [date_start],
        "date_end" : [date_end],
        "match_name": [match_name],
        "match_number" : [match_number],
        "gender" : [gender],
        "match_type": [match_type],
        "match_type_number" : [match_type_number],
        "official_data" :[json.dumps(official_data)],
        "winner": [winner],
        "decision_by" : [decision_by],
        "overs": [overs],
        "player_of_match" : [player_of_match],
        "team1" : [team1],
        "team1_id": [team1_id],
        "team1_players": [json.dumps(team1_players)],
        "team2": [team2],
        "team2_id": [team2_id],
        "team2_players": [json.dumps(team2_players)],
        "season": [season],
        "team_type" : [team_type],
        "toss_decision" : [toss_decision],
        "toss_winner": [toss_winner],
        "venue": [venue]

    })
    return match_info_df


In [243]:
def write_match_info(match_info_df: pd.DataFrame):
    match_info_tuples = match_info_df.values.tolist()

    #write to database
    table_name = 'match_info'
    columns = ', '.join(match_info_df.columns)
    sql = f"INSERT INTO {table_name} ({columns}) VALUES ({', '.join(['%s'] * len(match_info_df.columns))})"

    # Execute the INSERT statement for each row
    cursor = cnx.cursor()
    for row in match_info_tuples:
        try:
            cursor.execute(sql, row)
            cnx.commit()
            print(f"1 row inserted successfully into {table_name} table!")
        except mysql.connector.IntegrityError:
            print("Duplicate! Skipping...")

    cursor.close()
    

Innings and Innings_summary Data now:

In [ ]:
#to ensure the data in the match type and innings table "line" up, after writing the data to matches table,
#need to query it and then get the corresopnding match_id

In [323]:
def parse_innings_info(json_data: dict, match_info_df: pd.DataFrame):

    # get distinct match_id from the match_info table
    cursor = cnx.cursor()
    query = """
    SELECT MAX(match_id) -- this will be themost recent match_id
    FROM match_info 
    """

    # Extract the values from the DataFrame
    # city = match_info_df['city'].values[0]

    # date_end = match_info_df['date_end'].values[0]

    # match_name = match_info_df['match_name'].values[0]

    # try:
    #     match_number = float(match_info_df['match_number'].values[0])
    # except TypeError: #if match number doesnt exist, it will be NoneType
    #     match_number = 'NULL'

    # match_type_number = float(match_info_df['match_type_number'].values[0])

    # Execute the query with the provided values as parameters
    # cursor.execute(query, (city, date_end, match_name, match_number, match_type_number))

    cursor.execute(query)
    match_id = cursor.fetchall()[0][0]
    print("cursor.fetchall():", match_id)
     #this is the match_id that needs to be written to the innings table
    cursor.close()

    #get the team ids by querying the teams table
    team_lst = []
    over_lst = []
    batter_lst = []
    bowler_lst = []
    non_striker_lst = []
    batter_runs_lst = []
    extra_runs_lst = [] 
    extras_lst = []
    wicket_lst = []
    wicket_info_lst = []

    #add match_id and match_number to the dataframe at the end



    #loop through all the overs for both teams #TODO 3 for loops is disgusting
    for i in range(len(json_data['innings'])): #len is pretty much always 2
        #i will correspond to the team: 0 is team 1, 1 is team 2
        for over_idx, over in enumerate(json_data['innings'][i]['overs']):

            for delivery in over['deliveries']:

                team_lst.append(json_data['innings'][i]['team']) 
            
                over_lst.append(over['over']) #the over
                
                batter_lst.append(delivery['batter']) #get batter

                bowler_lst.append(delivery['bowler']) #get bowler

                # extras_lst.append(delivery['extras']) #the extras list
                
                non_striker_lst.append(delivery['non_striker']) #get non_striker

                
                batter_runs_lst.append(delivery['runs']['batter'])
                extra_runs_lst.append(delivery['runs']['extras'])

                try:
                    wicket_lst.append(json.dumps(delivery['wickets'][0]))
                except:
                    wicket_lst.append(None)
            
      
    innings_df = pd.DataFrame({
    "team": team_lst,
    "over_num": over_lst,
    "batter": batter_lst,
    "bowler": bowler_lst,
    "non_striker": non_striker_lst,
    "batter_runs": batter_runs_lst,
    "extra_runs": extra_runs_lst,
    "wickets": wicket_lst
    # "wicket_info": wicket_info_lst
    })
    innings_df['match_id'] = match_id


    return innings_df


    
    

In [191]:

innings_df =  parse_innings_info(json_data = json_data, match_info_df = match_info_df)

In [195]:
# def write_innings_info(innings_info_df: pd.DataFrame):
#     """ write innings_df to innings_info table"""


#     innings_info_tuples = innings_info_df.values.tolist()

#     #write to database
#     table_name = 'innings_info'
#     columns = ', '.join(innings_info_df.columns)
    
#     sql = f"INSERT INTO {table_name} ({columns}) VALUES ({', '.join(['%s'] * len(innings_info_df.columns))})"
     

#     # Execute the INSERT statement with the data
#     cursor = cnx.cursor()
#     try:
#         cursor.executemany(sql, innings_info_tuples)
#         print(f"{cursor.rowcount} rows inserted successfully into {table_name} table!")
#     except:
#         print("Duplicate Data! Skipping...")
#     cnx.commit()
   

    

In [245]:
def write_innings_info(innings_info_df: pd.DataFrame):
    innings_info_tuples = innings_info_df.values.tolist()

    #write to database
    table_name = 'innings_info'
    columns = ', '.join(innings_info_df.columns)
    sql = f"INSERT INTO {table_name} ({columns}) VALUES ({', '.join(['%s'] * len(innings_info_df.columns))})"

    # Execute the INSERT statement for each row
    cursor = cnx.cursor()
    for row in innings_info_tuples:
        try:
            cursor.execute(sql, row)
            print(f"1 row inserted successfully into {table_name} table!")
        except mysql.connector.IntegrityError:
            print("Duplicate Data! Skipping...")

    cnx.commit()
    cursor.close()

In [ ]:
write_innings_info(innings_info_df=innings_df)

## TESTING

In [ ]:
#read data to see what the fuck it looks like
with open('/Users/collinkennedy/Dropbox/R_dropbox/Zelus_Analytics/odis_json/64827.json', 'r') as file:
    json_data = json.load(file)



# def process_json_file(file_path):
#     with open(file_path, 'r') as file:
#         json_data = json.load(file)
#         # Perform data preprocessing on the json_data
#         # Return the preprocessed data
#         return (json_data)
#
file_paths = [os.path.join(folder_path, filename) for filename in os.listdir(folder_path) if filename.endswith('.json')]



In [247]:
file_paths[4]

'/Users/collinkennedy/Dropbox/R_dropbox/Zelus_Analytics/odis_json/647251.json'

In [325]:
with open('/Users/collinkennedy/Dropbox/R_dropbox/Zelus_Analytics/odis_json/760889.json', 'r') as file:
        json_data = json.load(file)

In [326]:
json_data['info']

{'balls_per_over': 6,
 'city': 'Dublin',
 'dates': ['2015-05-08'],
 'gender': 'male',
 'match_type': 'ODI',
 'match_type_number': 3650,
 'officials': {'match_referees': ['DT Jukes'],
  'reserve_umpires': ['R Black'],
  'umpires': ['M Hawthorne', 'IN Ramage']},
 'outcome': {'result': 'no result'},
 'overs': 50,
 'players': {'England': ['JWA Taylor',
   'ZS Ansari',
   'JM Bairstow',
   'TT Bresnan',
   'ST Finn',
   'AD Hales',
   'AU Rashid',
   'JJ Roy',
   'JM Vince',
   'DJ Willey',
   'MA Wood'],
  'Ireland': ['WTS Porterfield',
   'PR Stirling',
   'EC Joyce',
   "NJ O'Brien",
   'A Balbirnie',
   'GC Wilson',
   "KJ O'Brien",
   'GH Dockrell',
   'AR Cusack',
   'JF Mooney',
   'CA Young']},
 'registry': {'people': {'A Balbirnie': '6ef13460',
   'AD Hales': '92aeac25',
   'AR Cusack': '568e5a4a',
   'AU Rashid': '249d60c9',
   'CA Young': 'bd0a4a7d',
   'DJ Willey': '7f048519',
   'DT Jukes': '7c215d14',
   'EC Joyce': 'a48fc79d',
   'GC Wilson': '05de1a5a',
   'GH Dockrell': '99

In [324]:

#establish database connection 
import mysql.connector
import sqlalchemy

#connect to MySQL database cricket_db
cnx = mysql.connector.connect(user='webmaster', password='Zelus2cool123',
                              database='cricket_db')

#set folder path
folder_path = "/Users/collinkennedy/Dropbox/R_dropbox/Zelus_Analytics/odis_json"

#put all the file paths in a list
file_paths = [os.path.join(folder_path, filename) for filename in os.listdir(folder_path) if filename.endswith('.json')]



for idx,file in enumerate(file_paths):

    print("Parsing {}th file... ".format(idx))
    print("file path: {}".format(file))
    with open(file, 'r') as file:
        json_data = json.load(file)

    #get team and player information from the json
    team_df, player_df = parse_team_player_info(json_data = json_data)

    #write info to cricket_db
    write_players_to_cricket_db(player_df = player_df)
    write_teams_to_cricket_db(team_df=team_df)

    #get match information
    match_info_df = parse_match_info(json_data=json_data)

    #write match info to database
    write_match_info(match_info_df=match_info_df )

    #get innings information
    innings_df = parse_innings_info(json_data = json_data, match_info_df=match_info_df)

    #write to cricket_db
    write_innings_info(innings_info_df = innings_df)




    
        

    

Parsing 0th file... 
file path: /Users/collinkennedy/Dropbox/R_dropbox/Zelus_Analytics/odis_json/467883.json
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
Duplicate! Skipping...
team1 India
team2:  New Zealand
[(656,)]
Duplicate! Skipping...
cursor.fetchall(): 475
1 row inserted successfully into innings_info table!
1 row inserted successfully into innings_info table!
1 row inserted successfully into innings_info table!
1 row inserted successfully into innings_info table!
1 row inserted successfully into innings

KeyError: 'event'